## Refer the following video to mount AWS S3 to Databricks
<a href="https://www.youtube.com/watch?v=JRcgoyE_Tsc&ab_channel=DataFunX" target="_blank">Mount AWS S3 to Databricks</a>

In [0]:
aws_keys = spark.read.format("csv").option("header", "true").load("dbfs:/FileStore/shared_uploads/awskeys/rootkey.csv")

In [0]:
ACCESS_KEY = aws_keys.select("Access key ID").take(1)[0]['Access key ID']
SECRET_KEY = aws_keys.select("Secret access key").take(1)[0]['Secret access key']

In [0]:
import urllib

ENCODED_SECRET_KEY = urllib.parse.quote(string=SECRET_KEY, safe="")

In [0]:
AWS_S3_BUCKET = 'olympic-data-280623'
MOUNT_NAME = '/mnt/mount_s3'

SOURCE_URL = "s3a://%s:%s@%s" %(ACCESS_KEY, ENCODED_SECRET_KEY, AWS_S3_BUCKET)

In [0]:
dbutils.fs.mount(SOURCE_URL, MOUNT_NAME)

Out[14]: True

In [0]:
%fs ls '/mnt/mount_s3'

path name size modificationTime dbfs:/mnt/mount_s3/athlete_events.csv athlete_events.csv 23724678 1687925743000 dbfs:/mnt/mount_s3/athletes.csv athletes.csv 6071413 1687925771000

In [0]:
from pyspark.sql.types import StructType, StructField, IntegerType, StringType, FloatType

# schema for the athletes table
athletes_schema = StructType([
    StructField("id", IntegerType(), nullable=False),
    StructField("name", StringType(), nullable=False),
    StructField("gender", StringType(), nullable=True),
    StructField("height", IntegerType(), nullable=True),
    StructField("weight", FloatType(), nullable=True),
    StructField("team", StringType(), nullable=False)
])
# creating atheletes dataframe 
athletes_df = spark.read.format("csv").option("header", "true").schema(athletes_schema).load("dbfs:/mnt/mount_s3/athletes.csv")
# athletes_df = athletes_df.na.drop()

In [0]:
from pyspark.sql.types import StructType, StructField, IntegerType, StringType

# Define the schema for the athlete_events table
athlete_events_schema = StructType([
    StructField("athlete_id", IntegerType(), nullable=False),
    StructField("games", StringType(), nullable=False),
    StructField("year", IntegerType(), nullable=True),
    StructField("season", StringType(), nullable=True),
    StructField("city", StringType(), nullable=True),
    StructField("sport", StringType(), nullable=True),
    StructField("event", StringType(), nullable=True),
    StructField("medal", StringType(), nullable=True)
])

# creating athlete_events dataframe 

athlete_events_df = spark.read.format("csv").option("header", "true").schema(athlete_events_schema).load("dbfs:/mnt/mount_s3/athlete_events.csv")

athlete_events_df = athlete_events_df.na.drop()

In [0]:
# Use this command in Snowflake Worksheet to Grant access

# -- GRANT SELECT ON TABLE OLYMPIC_DB.PUBLIC.ATHLETES TO ROLE ACCOUNTADMIN;

# -- GRANT SELECT ON TABLE OLYMPIC_DB.PUBLIC.ATHLETE_EVENTS TO ROLE ACCOUNTADMIN;

In [0]:
# Snowflake Connection credentials
sfOptions = {
  "sfUrl": "zf64891.central-india.azure.snowflakecomputing.com",
  "sfUser": "Snowflake-UserName",
  "sfPassword": "Snowflake-Password",
  "sfDatabase": "OLYMPIC_DB",
  "sfSchema": "PUBLIC",
  "sfWarehouse": "COMPUTE_WH"
}

In [0]:

# Specify the Snowflake table name
table_name = "athletes"

# Write the DataFrame to Snowflake
athletes_df.write.format("snowflake") \
    .options(**sfOptions) \
    .option("dbtable", table_name) \
    .mode("overwrite") \
    .options(header=True) \
    .save()


In [0]:

# Specify the Snowflake table name
table_name = "athlete_events"

# Write the DataFrame to Snowflake
athlete_events_df.write.format("snowflake") \
    .options(**sfOptions) \
    .option("dbtable", table_name) \
    .mode("overwrite") \
    .options(header=True) \
    .save()

In [0]:

# Specify the Snowflake table name
table_name = "athlete_events"

# Read the data written by the previous cell back.
df = spark.read \
  .format("snowflake") \
  .options(**sfOptions) \
  .option("dbtable", table_name) \
  .load()
 
display(df)

ATHLETE_ID GAMES YEAR SEASON CITY SPORT EVENT MEDAL 120259 2016 Summer 2016 Summer Rio de Janeiro Table Tennis Table Tennis Women's Team NA 120260 1956 Summer 1956 Summer Melbourne Boxing Boxing Men's Welterweight Silver 120261 1968 Summer 1968 Summer Mexico City Athletics Athletics Men's Decathlon NA 120262 1992 Summer 1992 Summer Barcelona Athletics Athletics Women's Long Jump NA 120262 2000 Summer 2000 Summer Sydney Athletics Athletics Women's Long Jump NA 120263 1964 Winter 1964 Winter Innsbruck Luge Luge Men's Singles NA 120264 1904 Summer 1904 Summer St. Louis Wrestling Wrestling Men's Light-Flyweight, Freestyle Bronze 120265 1948 Summer 1948 Summer London Hockey Hockey Men's Hockey Bronze 120265 1952 Summer 1952 Summer Helsinki Hockey Hockey Men's Hockey Silver 120266 1968 Summer 1968 Summer Mexico City Volleyball Volleyball Men's Volleyball NA 120267 1968 Summer 1968 Summer Mexico City Athletics Athletics Women's 200 metres NA 120267 1968 Summer 1968 Summer Mexico City Athletics Athletics Women's 4 x 100 metres Relay NA 120267 1968 Summer 1968 Summer Mexico City Athletics Athletics Women's Pentathlon NA 120268 2012 Summer 2012 Summer London Shooting Shooting Women's Air Pistol, 10 metres NA 120268 2012 Summer 2012 Summer London Shooting Shooting Women's Sporting Pistol, 25 metres NA 120269 1952 Summer 1952 Summer Helsinki Boxing Boxing Men's Bantamweight NA 120270 1996 Summer 1996 Summer Atlanta Athletics Athletics Women's High Jump NA 120271 1968 Summer 1968 Summer Mexico City Boxing Boxing Men's Light-Welterweight NA 120271 1972 Summer 1972 Summer Munich Boxing Boxing Men's Light-Middleweight Bronze 120272 2016 Summer 2016 Summer Rio de Janeiro Athletics Athletics Men's 5,000 metres NA 120273 1988 Summer 1988 Summer Seoul Athletics Athletics Women's 100 metres NA 120273 1988 Summer 1988 Summer Seoul Athletics Athletics Women's 200 metres NA 120274 1928 Summer 1928 Summer Amsterdam Athletics Athletics Men's 400 metres NA 120275 2004 Summer 2004 Summer Athina Football Football Men's Football NA 120276 1968 Summer 1968 Summer Mexico City Rowing Rowing Men's Coxed Eights Gold 120277 1900 Summer 1900 Summer Paris Rowing Rowing Men's Coxed Fours Gold 120277 1900 Summer 1900 Summer Paris Rowing Rowing Men's Coxed Eights NA 120278 1996 Summer 1996 Summer Atlanta Boxing Boxing Men's Middleweight NA 120279 1976 Summer 1976 Summer Montreal Handball Handball Women's Handball Silver 120279 1980 Summer 1980 Summer Moskva Handball Handball Women's Handball Bronze 120280 2008 Summer 2008 Summer Beijing Baseball Baseball Men's Baseball Bronze 120281 1936 Summer 1936 Summer Berlin Athletics Athletics Women's 80 metres Hurdles NA 120282 1980 Summer 1980 Summer Moskva Wrestling Wrestling Men's Middleweight, Freestyle NA 120283 2000 Summer 2000 Summer Sydney Athletics Athletics Women's Long Jump NA 120283 2000 Summer 2000 Summer Sydney Athletics Athletics Women's Heptathlon NA 120283 2008 Summer 2008 Summer Beijing Athletics Athletics Women's Long Jump NA 120283 2012 Summer 2012 Summer London Athletics Athletics Women's Long Jump NA 120284 1972 Winter 1972 Winter Sapporo Speed Skating Speed Skating Women's 3,000 metres NA 120285 1964 Summer 1964 Summer Tokyo Swimming Swimming Women's 400 metres Freestyle NA 120286 2000 Summer 2000 Summer Sydney Athletics Athletics Men's 800 metres NA 120287 1936 Winter 1936 Winter Garmisch-Partenkirchen Cross Country Skiing Cross Country Skiing Men's 18 kilometres NA 120287 1936 Winter 1936 Winter Garmisch-Partenkirchen Cross Country Skiing Cross Country Skiing Men's 4 x 10 kilometres Relay NA 120288 2008 Summer 2008 Summer Beijing Wrestling Wrestling Men's Middleweight, Freestyle Silver 120288 2012 Summer 2012 Summer London Wrestling Wrestling Men's Middleweight, Freestyle NA 120289 2008 Summer 2008 Summer Beijing Wrestling Wrestling Men's Heavyweight, Freestyle Silver 120289 2012 Summer 2012 Summer London Wrestling Wrestling Men's Heavyweight, Freestyle NA 120290 2000 Summer 2000 Summer Sydney Judo Jud

In [0]:
# Specify the Snowflake table name
table_name = "athletes"

# Read the data written by the previous cell back.
df = spark.read \
  .format("snowflake") \
  .options(**sfOptions) \
  .option("dbtable", table_name) \
  .load()
 
display(df)

ID NAME GENDER HEIGHT WEIGHT TEAM 94427 Prisca Philip (-Polzine) F null null Barbados 94428 Andrea Philipp (-Ziercke) F 165 60.0 Germany 94429 Hugo Philipp M null null Austria 94430 Lutz Philipp M 178 69.0 Germany 94431 Luzius Philipp M 170 77.0 Switzerland 94432 Peter Philipp M 183 73.0 Switzerland 94433 Rainer Philipp M 182 88.0 West Germany 94434 Ludo Ren Mathilde Philippaerts M 180 85.0 Belgium 94435 Nicola Philippaerts M 186 76.0 Belgium 94436 Bernard Philippe M 179 73.0 Luxembourg 94437 Franois Philippe M 175 75.0 France 94438 Gildas Philippe M 173 58.0 France 94439 Marcel Philippe M 178 68.0 France 94440 Xavier Philippe M 191 97.0 France 94441 Karine Laurent Philippot (-Laurent) F 167 56.0 France 94442 Mark Anthony Philippoussis M 193 91.0 Australia 94443 Louis Philipps M 160 49.0 France 94444 Marjolein Philipsen F 167 60.0 Netherlands 94445 Nicolai Philipsen M null null Denmark 94446 "Maria Johanna ""Zus"" Philipsen-Braun" F 170 null Netherlands 94447 Sissy Anette Philipsson F 165 54.0 Sweden 94448 Christine Phillip (Zahn-) F 164 60.0 East Germany 94449 Elinah Amani Phillip F 164 50.0 British Virgin Islands 94450 Emrol Phillip M null null Grenada 94451 Jincy Phillip F 173 58.0 India 94452 Joel Japheth Phillip M 188 75.0 Grenada 94453 Njisane Nicholas Phillip M 185 88.0 Trinidad and Tobago 94454 Phillippot M null null France 94455 Phillips M null null Great Britain 94456 Alan Phillips M 184 84.0 South Africa 94457 Alfred Henry Phillips M null null Canada 94458 Amanda Susan Phillips F 164 63.0 Australia 94459 Andr Lamar Phillips M 188 84.0 United States 94460 Andrew Phillips M 167 71.0 Jamaica 94461 Anthony Phillips M 147 56.0 Barbados 94462 Belinda Phillips F 160 50.0 Jamaica 94463 "Herbert Thorne ""Bertie"" Phillips" M null null South Africa 94464 Brenda Joan Phillips F 155 49.0 Zimbabwe 94465 Brian Phillips M 189 80.0 Canada 94466 "Chester Wilson ""Chet"" Phillips" M null null United States 94467 Daniel Phillips M 181 80.0 Australia 94468 David Brad Phillips M 178 76.0 New Zealand 94469 Dwight D. Phillips M 185 73.0 United States 94470 Eric Phillips M 174 68.0 Venezuela 94471 Erin Victoria Phillips F 173 70.0 Australia 94472 Frederick Gordon Phillips M null null Wales-4 94473 Glenda May Phillips (-Adams) F 169 70.0 Great Britain 94474 Harper Phillips M null null United States 94475 "Henry John ""Harry"" Phillips" M null null South Africa 94476 Hayden Phillips M 180 72.0 New Zealand 94477 "Hector ""Hec"" Phillips" M 175 null Canada 94478 Henry Phillips M 184 109.0 Panama 94479 Hermon Edgar Phillips M 178 68.0 United States 94480 Isa Phillips M 193 84.0 Jamaica 94481 Jesse Phillips M 189 82.0 Australia 94482 "Joseph ""Joe"" Phillips" M null null India 94483 Karen Anne Phillips (-Higgison) F 170 58.0 Australia 94484 Krista Lynn Phillips F 198 104.0 Canada 94485 Liam Peter Phillips M 181 85.0 Great Britain 94486 Marjorie Acker Phillips F null null United States 94487 Mark Anthony Peter Phillips M 185 79.0 Great Britain 94488 Merilyn Phillips F 170 57.0 Cayman Islands 94489 Mollie Doreen Phillips F 160 null Great Britain 94490 Owen D. Phillips M 175 76.0 Belize 94491 Peter Robin Phillips M 178 110.0 Australia 94492 Richard Phillips M 188 76.0 Jamaica 94493 Sarah Phillips F 168 57.0 Great Britain 94494 "Tracey Elizabeth ""Traci"" Phillips" F 162 55.0 United States 94495 "Vadivelu ""V. J."" Phillips" M 170 59.0 India 94496 William John Berge Phillips M null null Australia 94497 Zara Anne Elizabeth Phillips (-Tindall) F 168 64.0 Great Britain 94498 William Philo M null null Great Britain 94499 David Philp M null null Fiji 94500 "Anthony Stephen ""Tony"" Philp Jr." null 172.0 73 94501 Trevor Wansbrough Philp M 181 80.0 Canada 94502 Colin Philp, Jr. M 183 80.0 Fiji 94503 Anthony Colin Philp, Sr. M 181 85.0 Fiji 94504 Davis Welsh Phinney M 172 75.0 United States 94505 Taylor Phinney M 196 81.0 United States 94506 Dhira Phiphobmongkol M 166 55.0 Thailand 94507 Angela Phipps F 175 57.0 Canada 94508 Carmen Lilith Phipps (-Laing) F 